In [5]:
import tensorflow as tf
import pandas as pd
from hyperopt import fmin, hp, tpe, STATUS_OK

from tensorflow import keras

In [6]:
train_raw = pd.read_csv('data/train.csv').drop('id', axis=1).to_numpy()
split = int(train_raw.shape[0] * .7)
X_train = train_raw[:split, :14]
y_train = train_raw[:split, 14:]
X_valid = train_raw[split:, :14]
y_valid = train_raw[split:, 14:]

In [13]:
search_space = {
    'activation': hp.choice('activation', ('relu', 'selu', 'elu')),
    'units': hp.choice('units', (4, 5, 6)),
    'distorting_layer': hp.choice(
        'distorting_layer',
        (
            keras.layers.Dropout(.2),
            keras.layers.Dropout(.3),
            keras.layers.Dropout(.4),
            keras.layers.GaussianNoise(.01),
            keras.layers.GaussianNoise(.02),
            keras.layers.GaussianNoise(.03),
            keras.layers.GaussianNoise(.1),
            keras.layers.GaussianNoise(.2)
        ))
}


def nn_objective(space: dict) -> dict:
    encoder = keras.models.Sequential([
        keras.layers.Dense(14, activation=space['activation']),
        space['distorting_layer'],
        keras.layers.Dense(space['units'], activation=space['activation'])
    ])
    decoder = keras.models.Sequential([
        keras.layers.Dense(space['units'] * 2, activation=space['activation']),
        keras.layers.Dense(14, activation=space['activation'])
    ])
    denoising_ae = keras.models.Sequential([encoder, decoder])

    denoising_ae.compile(optimizer='adam', loss='mse')
    denoising_ae.fit(X_train, X_train, epochs=20, batch_size=32)

    acc = denoising_ae.evaluate(X_valid, X_valid, verbose=0)

    return {'loss': -acc, 'status': STATUS_OK}

In [ ]:
best_params = fmin(
    fn=nn_objective,
    space=search_space,
    algo=tpe.suggest,
    max_evals=50)

Epoch 1/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0169

Epoch 2/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0081

Epoch 3/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0078

Epoch 4/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0076

Epoch 5/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0073

Epoch 6/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0071

Epoch 7/20                                            

6563/6563 [==============================] - 16s 2ms/step - loss: 0.0069

Epoch 8/20                                            

6563/6563 [=======================